In [233]:
import numpy as np
import nltk
import re
import pandas as pd 
import json
import os
import pickle
import csv
import matplotlib.pyplot as plt

from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words
from string import punctuation

from sklearn.preprocessing import normalize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy import spatial

from ast import literal_eval

from urllib.parse import urlparse

nltk.download('words')
th_stop = thai_stopwords()
en_stop = get_stop_words('en')
p_stemmer = PorterStemmer()

dup_check = []

def split_word(text):
    tokens = word_tokenize(text,engine='newmm')
    
    # Remove stop words ภาษาไทย และอักขระพิเศษ
    tokens = [i for i in tokens if (not i in th_stop) & (not i in en_stop) & (not i in punctuation) & (not i in ["'",'"','“','”','‘','’','\n',"None", ' '])] 
    
    # ลบตัวเลข
    tokens = [i for i in tokens if not i.isnumeric()]
    
    # ลบช่องว่าง
    tokens = [i for i in tokens if not ' ' in i]

    return tokens

def remove_emojis(data):
    emoj = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)
    return re.sub(emoj, '', data)

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\Administrator\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


## ดึงข้อมูลของ cofact

### ดึงส่วนอ้างอิงของ cofact

In [234]:
def read_cofact_refer(): #สำหรับดึงข้อมูลของ cofact csv
    global dup_check
    
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Cofact/old/cofact_refer_old.csv')
    
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)

    # read header from CSV file
    header = []
    header = next(csvreader)
    
    rows = []
    dup_check = []
    
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        # เพิ่ม header และตรวจสอบว่า header ซ้ำหรือไม่
        if row[1] in dup_check:
            continue
        
        elif row[1] not in dup_check:
            dup_check.append(row[1])
            tmp.append(row[1]) 

        # เพิ่ม content
        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        
        tmp.append(content)
        
        # เพิ่ม link (ข่าวต้นทางสุด)
        tmp.append(row[3])
        
        # เพิ่ม link (ลิงค์บนเว็บไซต์ cofact)
        tmp.append(row[5])
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [235]:
cofact_refer_text_list = read_cofact_refer()

In [236]:
len(cofact_refer_text_list)

2050

### ดึงส่วนคนถามของ cofact

In [237]:
def read_cofact_info(): #สำหรับดึงข้อมูลของ cofact info csv
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Cofact/old/cofact_info_old.csv')
    
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)

    # read header from CSV file
    header = []
    header = next(csvreader)
    
    rows = []
    info_dup_check = []
    
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        # เพิ่ม ส่วนที่คนถาม (query) + ตรวจสอบว่า query ซ้ำหรือไม่
        if row[1] in info_dup_check:
            continue
        
        elif row[1] not in info_dup_check:
            info_dup_check.append(row[1])
            tmp.append(row[1])

        # เพิ่ม link (ลิงค์บนเว็บไซต์ cofact)
        tmp.append(row[3]) 
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [238]:
cofact_info_text_list = read_cofact_info()

In [240]:
len(cofact_info_text_list)

3547

In [241]:
matched_list = []

for i in range(len(cofact_refer_text_list)):
    for j in range(len(cofact_info_text_list)):
        tmp = []
        if cofact_info_text_list[j][1] == cofact_refer_text_list[i][3]:
            tmp.append(cofact_info_text_list[j][0])
            tmp.append(cofact_refer_text_list[i][0])
            matched_list.append(tmp)

In [242]:
len(matched_list)

1704

In [243]:
matched_list

[['น้ำชา รักษาอาการแพ้อาหารได้',
  'น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเชื่อ'],
 ['เอามะนาวกับเกลือมาถูหน้าผาก แก้ไมเกรนได้',
  'มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ'],
 ['พบการโฆษณาจำหน่ายผลิตภัณฑ์ NANO SILVER Sanitizer Water Spray ทางสื่อออนไลน์ว่า ช่วยฆ่าเชื้อโรค เชื้อไวรัสและแบคทีเรียได้มากกว่า 3,000 ชนิด สามารถฉีดใส่มาส์กได้โดยไม่ทำลายมาส์ก แถมยังช่วยเพิ่มประสิทธิภาพในการป้องกันและทำลายเชื้อโรค ฆ่าเชื้อโรคต่อเนื่องนาน 8-10 ชั่วโมง อีกทั้งช่วยลดสิว ผดผื่น อาการแพ้ตามผิวหนัง โดยได้การรับรองจากมหาวิทยาลัยและหน่วยงานต่างๆ',
  'อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสและแบคทีเรีย'],
 ['ดื่มกาแฟทำให้หน้าอกเล็กลง',
  'ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง '],
 ['นำปิโตรเลี่ยมเจลลี่มาทาคิ้ว แล้วคิ้วหนาขึ้นได้',
  'คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริง'],
 ['เชื้อ ‘ไวรัสโคโรนา’ อาจจะเป็นอาวุธชีวภาพที่คนสร้างขึ้นมา',
  'อย่าหลงเชื่อ! ‘อ.เจษฎ์’ ยัน ‘ไวรัสโคโรนา’ ถูกตัดต่อพันธุกรรมผสม HIV เป็นอาวุธชีวภาพ ไม่เป็นความจริง'],
 ['ช่อง 9 เพิ่งออกข่าวภาคค่ำ วันนี้จ๊ะ.ตอ

### นำ query ซ้ำใน matched list ออก

In [244]:
matched_list_dup_check = []
dup_del_matched_list = []

for query in matched_list:
    if query[0] in matched_list_dup_check:
        continue
    elif query[0] not in matched_list:
        matched_list_dup_check.append(query[0])
        dup_del_matched_list.append(query)

In [245]:
dup_del_matched_list

[['น้ำชา รักษาอาการแพ้อาหารได้',
  'น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเชื่อ'],
 ['เอามะนาวกับเกลือมาถูหน้าผาก แก้ไมเกรนได้',
  'มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ'],
 ['พบการโฆษณาจำหน่ายผลิตภัณฑ์ NANO SILVER Sanitizer Water Spray ทางสื่อออนไลน์ว่า ช่วยฆ่าเชื้อโรค เชื้อไวรัสและแบคทีเรียได้มากกว่า 3,000 ชนิด สามารถฉีดใส่มาส์กได้โดยไม่ทำลายมาส์ก แถมยังช่วยเพิ่มประสิทธิภาพในการป้องกันและทำลายเชื้อโรค ฆ่าเชื้อโรคต่อเนื่องนาน 8-10 ชั่วโมง อีกทั้งช่วยลดสิว ผดผื่น อาการแพ้ตามผิวหนัง โดยได้การรับรองจากมหาวิทยาลัยและหน่วยงานต่างๆ',
  'อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสและแบคทีเรีย'],
 ['ดื่มกาแฟทำให้หน้าอกเล็กลง',
  'ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง '],
 ['นำปิโตรเลี่ยมเจลลี่มาทาคิ้ว แล้วคิ้วหนาขึ้นได้',
  'คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริง'],
 ['เชื้อ ‘ไวรัสโคโรนา’ อาจจะเป็นอาวุธชีวภาพที่คนสร้างขึ้นมา',
  'อย่าหลงเชื่อ! ‘อ.เจษฎ์’ ยัน ‘ไวรัสโคโรนา’ ถูกตัดต่อพันธุกรรมผสม HIV เป็นอาวุธชีวภาพ ไม่เป็นความจริง'],
 ['ช่อง 9 เพิ่งออกข่าวภาคค่ำ วันนี้จ๊ะ.ตอ

In [246]:
len(dup_del_matched_list)

1611

In [247]:
all_refer_text_list = []
all_refer_text_list = cofact_refer_text_list

In [248]:
len(all_refer_text_list)

2050

## ------------------------------------------------------------------------------
## สร้าง dataframe ของ cofact สำหรับอ้างถึงตอนแนบลิงค์ url แสดงผล

In [249]:
all_refer_header = []
all_refer_content = []
all_refer_url = []
all_refer_datetime = []
all_refer_domain = []

for i in range(len(all_refer_text_list)):
    all_refer_header.append(all_refer_text_list[i][0]) #list ของส่วนหัวข้อข่าว
    all_refer_content.append(all_refer_text_list[i][1]) #list ของส่วนเนื้อหาเท่านั้น
    all_refer_url.append(all_refer_text_list[i][2]) #list ของ url เท่านั้น
    all_refer_datetime.append(all_refer_text_list[i][3]) #list ของ datetime เท่านั้น
    all_refer_domain.append(urlparse(all_refer_text_list[i][2]).hostname) #list ของ domain เท่านั้น


In [250]:
#ทำ list ให้เป็น dataframe
all_original_text_and_headline_news_df = pd.DataFrame(list(zip(all_refer_header, all_refer_content, all_refer_url, all_refer_datetime, all_refer_domain)), columns=["All_headline_from_every_reference", "All_content_from_every_reference", "All_URL_from_every_reference", "All_datatime_from_every_reference", "All_domain_from_every_reference"])

all_original_text_and_headline_news_df

All_headline_from_every_reference  \
0     น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเ...   
1               มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ   
2     อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสแล...   
3         ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง    
4            คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริง   
...                                                 ...   
2045  โควิด-19 : นมตราหมี ยาฆ่าพยาธิ และน้ำมันหอมระเ...   
2046  โควิด : WHO ให้ชื่อ "โอไมครอน" สายพันธุ์ใหม่ที...   
2047  ยูเอ็นเปิดผลศึกษาคดีข่มขืนในไทย-เวียดนาม ผู้หญ...   
2048  WHO : อุบัติเหตุบนท้องถนนทำให้คนหนุ่มสาวเสียชี...   
2049  ศูนย์จีโนมฯ ระบุโควิด- 19 ใกล้ End game กลายเป...   

                       All_content_from_every_reference  \
0     มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรัก...   
1     เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว...   
2     อย. เตือน!! อย่าหลงเชื่อผลิตภัณฑ์ NANO SILVER ...   
3     กาแฟเป็นเครื่องดื่มที่นิยมอย่างแพร่หลายทั่วโลก...   
4     แชร์ทั่วอินเทอร์เน็ตว่า มีคนนำปิโตรเลียม เจลลี...   
...                                                 ...   
2045  โรงพยาบาลต่าง ๆ กำลังประสบปัญหาคนไข้ล้น และการ...   
2046  WHO แถลงเมื่อวันที่ 26 พ.ย. ว่าเชื้อนี้มีการกล...   
2047  องค์การเพื่อการส่งเสริมความเสมอภาคระหว่างเพศแล...   
2048  WHO เผยแพร่ตัวเลขที่ชี้ให้เห็นว่าทวีปแอฟริกามี...   
2049  ศูนย์จีโนมทางการแพทย์ คณะแพทย์ศาสตร์ โรงพยาบาล...   

                           All_URL_from_every_reference  \
0     https://sure.oryor.com/index.php/detail/media_...   
1     https://sure.oryor.com/index.php/detail/media_...   
2     https://oryor.com/%E0%B8%AD%E0%B8%A2/detail/me...   
3     https://sure.oryor.com/index.php/detail/media_...   
4     https://sure.oryor.com/index.php/detail/media_...   
...                                                 ...   
2045    https://www.bbc.com/thai/international-57901266   
2046    https://www.bbc.com/thai/international-59428316   
2047         https://www.bbc.com/thai/thailand-42170733   
2048    https://www.bbc.com/thai/international-46545106   
2049          https://news.thaipbs.or.th/content/311692   

             All_datatime_from_every_reference All_domain_from_every_reference  
0     https://cofact.org/article/18fondmkdx5t1                  sure.oryor.com  
1      https://cofact.org/article/rzoplz5v22rb                  sure.oryor.com  
2     https://cofact.org/article/110yfgvyqqj5d                       oryor.com  
3     https://cofact.org/article/2wmt8eex5xqcg                  sure.oryor.com  
4     https://cofact.org/article/288f0qlim28fh                  sure.oryor.com  
...                                        ...                             ...  
2045  https://cofact.org/article/1zctvpcnaf09t                     www.bbc.com  
2046   https://cofact.org/article/lbsaldkysx4t                     www.bbc.com  
2047  https://cofact.org/article/1r33jgmldh36l                     www.bbc.com  
2048   https://cofact.org/article/7pxib0bvohpq                     www.bbc.com  
2049  https://cofact.org/article/1wia7tfbojy4q              news.thaipbs.or.th  

[2050 rows x 5 columns]

In [251]:
all_headline_tokens_list = [split_word(txt) for txt in all_refer_header] #นำ list ของหัวข้อข่าวมาตัดคำ

In [252]:
all_tokens_list_j = [','.join(tkn) for tkn in all_headline_tokens_list]

----------------------------------------------------------------------------------
# สร้าง vocabulary set

In [253]:
print(all_tokens_list_j[0].split(",")[0:2])


['น้ำชา', 'รักษาโรค']


In [254]:
## Create Vocabulary
tokens_list = []

for words in all_tokens_list_j:
    # print(words)
    temp_list = words.split(",")
    # print(temp_list)
    for i in temp_list:
        tokens_list.append(i)

vocabulary = set(tokens_list)
vocabulary = list(vocabulary)

In [255]:
len(vocabulary)

4513

--------------------------------------------------------------------------------------

In [256]:
tvec = TfidfVectorizer(analyzer=lambda x:x.split(','),)
original_c_feat = tvec.fit_transform(all_tokens_list_j)

### Save Trained TFID Model

In [257]:
### Save model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
with open(path,'wb') as handle:
    pickle.dump(original_c_feat, handle)

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


In [258]:
### load model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
t = pickle.load(open(path,'rb'))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


### Save Vocabulary

In [259]:
### Save Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "w", encoding="utf-8") as file:
    file.write(str(vocabulary))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [260]:
### load Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "r", encoding="utf-8") as file:
    data2 = eval(file.readline())

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [261]:
data2

['',
 'มีพิษ',
 'พริก',
 'แบน',
 'ห้องสมุด',
 'ผู้ยิ่งใหญ่',
 'ศรีสุวรรณ',
 'คาราโอเกะ',
 'เจ้าตัว',
 'กล้อง',
 'น้ำมัน',
 'แสวงบุญ',
 'โบราณ',
 'เด็กนักเรียน',
 'ทช.',
 'เบต้า',
 'เอือม',
 'ม.ค.',
 'เพ็ชร',
 'วิธี',
 'เงินฝาก',
 'ชายแดน',
 'ทัก',
 'น้ำผลไม้',
 'อาหรับ',
 'มอเตอร์ไซค์',
 'สื่อสาร',
 'แพ',
 'ปลาช่อน',
 'สิ้นลม',
 'ดาราศาสตร์',
 'มะกัน',
 'O',
 'เขน',
 'หน้า',
 'ปั่นหุ้น',
 'เมารถ',
 'ผู้การ',
 'คอนโด',
 'Bathing',
 'นูน',
 'ปา',
 'เด้ง',
 'ลูกหนัง',
 'ไฮบริด',
 'เป็นไปได้',
 'เคลียร์',
 'หายใจ',
 'ล้าน',
 'ประวัติศาสตร์',
 'สมรส',
 'คนร้าย',
 'หน่่อย!',
 'ไก่ทอด',
 'น้ำแข็ง',
 'สัญชาติ',
 'เคเอฟซี',
 'ข่าว',
 'อึ',
 'พันธ์',
 'แบ่งรับแบ่งสู้',
 'ตรากฎหมาย',
 'ทศพร',
 'พิมาย',
 'เหล้า',
 'ใช้จ่าย',
 'นวด',
 'PM',
 'Super',
 'เดลตา',
 'คาดการณ์',
 'ไข่ขาว',
 'มิถุนายน',
 'สปส.',
 'สิงคโปร์',
 'ขิง',
 'เซิร์ฟเวอร์',
 'กล้วยหอม',
 'โลหะ',
 'คนงาน',
 'ภาษาอังกฤษ',
 'ลอย',
 'ตัวการ',
 'รวย',
 'ทึ่ง',
 'ช็อกโกแลต',
 'อำเภอ',
 'วงเงิน',
 'ไมโคร',
 'สวิตเซอร์แลนด์',
 'แม่',
 'ขั

In [262]:
len(data2)

4513

## Create vector for Query/search keywords

In [263]:
## Create vector for Query/search keywords
def gen_vector_T(tokens):

    Q = np.zeros((len(vocabulary)))
    
    x = tvec.transform(tokens)
    
    x = x.A[0]
    return x

### Calculate Cosine similarity of trained Tfidf to input query


In [264]:
norm_original_c_feat = normalize(original_c_feat)
norm_original_c_feat = norm_original_c_feat.toarray()
norm_original_c_feat = norm_original_c_feat.T

In [265]:
query_vector = []
def cosine_similarity_T(k, query):
    tokens = split_word(str(query))
    q_df = pd.DataFrame(columns=['q_clean'])
    q_df.loc[0,'q_clean'] =str(tokens)

    q_df=q_df.replace(to_replace ="\[.", value = '', regex = True)
    q_df=q_df.replace(to_replace ="'", value = '', regex = True)
    q_df=q_df.replace(to_replace =" ", value = '', regex = True)
    q_df=q_df.replace(to_replace ='\]', value = '', regex = True)
    
    d_cosines = []
    
    query_vector = gen_vector_T(q_df['q_clean'])
    query_vector = query_vector.reshape((1,-1))

    d_cosines = np.dot(normalize(query_vector),norm_original_c_feat)
    
    list_d_cosines = d_cosines[0].tolist()
    
    out = np.array(list_d_cosines).argsort()[-k:][::-1]

    list_d_cosines.sort()
    a = pd.DataFrame()
    for i in out:
        a.loc[i,'index'] = str(i)
        a.loc[i,'headline'] = all_original_text_and_headline_news_df["All_headline_from_every_reference"][i]

    list_d_cosines.sort(reverse=True)
    
    for j in range(k):
        a.loc[out[j],'Score'] = list_d_cosines[j]
        
    return a

In [266]:
query = "สิ้นเดือนนี้ คิงส์พาวเวอร์ ปิดทุกสาขา ไม่มีกำหนด ยกเว้นสนามบิน สำนักงานใหญ่ซอยรางน้ำ ในยามปกติ ขายได้วันละ 50 ล้านบาท ตอนนี้ทุกวันขายได้วันละ 20,000 บาท"

In [267]:
%time all_result = cosine_similarity_T(30, query)

Wall time: 37 ms


In [268]:
all_result

index                                           headline     Score
1310  1310       ข่าวปลอม คิงเพาเวอร์ ปิดทุกสาขาสิ้นเดือนนี้   0.366449
1311  1311  “คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่า...  0.257978
1444  1444  เช็ก! จังหวัดไหนบ้าง ไม่ใส่หน้ากากออกจากบ้าน ป...  0.248821
555    555  เงินเข้าวันนี้ เยียวยา กลุ่มเปราะบาง รับครั้งเ...  0.167091
846    846  "คนละครึ่ง" เตรียมพร้อมให้รับสิทธิ์เงิน 3,000 ...  0.166953
280    280  ครม.ไฟเขียวจ่าย "เยียวยากลุ่มเปราะบาง" 13ล้านค...  0.165458
72      72  ใครบ้าง เข้าเกณฑ์ได้รับเงิน "เราไม่ทิ้งกัน" จา...  0.161012
1541  1541                  คลัง กู้เพิ่ม7แสนล้านบาท สู้โควิด  0.151592
901    901  เริ่มแล้ววันนี้! ลงทะเบียน คนละครึ่ง รับสิทธิเ...  0.140570
1566  1566  ข่าวปลอม อย่าแชร์! ธปท. ปล่อยคลิปเสียง แจกแจงแ...  0.133810
271    271  ใครครอบครอง 2 สารพิษ มีโทษจำคุก 10 ปี ปรับ 1 ล...  0.133364
202    202  เตือนระวังมิจฉาชีพ หลอกขาย'ตั๋วออนไลน์'ช่วงโควิด!  0.130338
241    241  เช็กด่วน "เยียวยานักกีฬา" กลุ่มไหนได้สิทธิ์รับ...  0.129262
1479  1479  ข่าวปลอม! ตลาดหลักทรัพย์แห่งประเทศไทย เปิดให้ล...  0.129075
1818  1818      ข่าวปลอมรัฐแจก 25,000 บาท ชาวน่านแห่ลงทะเบียน  0.127891
291    291  เยียวยาผู้พิการ 1,000 บาท เริ่มแจกเงินแล้ว ย้ำ...  0.127855
1019  1019   เริ่มแล้ว สมอ.ควบคุมผลิต-จำหน่าย “พาวเวอร์แบงก์”  0.127148
1065  1065  ข่าวบิดเบือน บัตรสวัสดิการแห่งรัฐช่วยเงินค่าน้...  0.126292
757    757    ราชกิจจาฯ ประกาศ ห้ามขาย "เหล้า-เบียร์" ออนไลน์  0.124860
665    665  คนไทย-ฟิลิปปินส์ ถูกหลอกออมทอง เสียหายกว่า 2 ล...  0.122615
1080  1080  ข่าวบิดเบือน รัฐฯ ช่วยเหลือคนพิการ แจกเงินคนละ...  0.122395
141    141  ย้ำชัดๆ 1-2 พ.ค. ผ่อนคลายให้ขายเหล้าได้หรือไม่...  0.122021
2039  2039  ปลั๊กไฟที่มีฟิวส์ ผิดกฎหมาย ห้ามซื้อ-ขาย จริงห...  0.120452
167    167  เปิด 5 จังหวัดที่ห้ามขายเหล้า-เบียร์ต่อ จนกว่า...  0.119929
1728  1728  ข่าวปลอม! เว็บ THVaccine.com เปิดลงทะเบียนจองฉ...  0.119757
132    132  ข่าวปลอม บัตรสวัสดิการแห่งรัฐ แจก 3,000 บาท ให...  0.118190
1725  1725  ข่าวปลอม อย่าแชร์! เว็บ THVaccine.com เปิดลงทะ...  0.117945
423    423     อย.เตือนอย่าเชื่อเว็บหลอกขาย “น้ำยาหยอดตานาโน”  0.117343
116    116        รวบนักศึกษา ทำธนบัตรปลอมขายให้กลุ่มยาเสพติด  0.115723
1693  1693  ครม.มีมติจ่ายเงินเยียวยา "ฟรีแลนซ์" ม.39-40 คน...  0.115672

In [269]:
all_result.iloc[1]['headline']

'“คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่าวเท็จ! รางน้ำ-พัทยา-ภูเก็ตเปิดตามปกติ'

In [270]:
all_result.iloc[:10]['headline']

1310         ข่าวปลอม คิงเพาเวอร์ ปิดทุกสาขาสิ้นเดือนนี้ 
1311    “คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่า...
1444    เช็ก! จังหวัดไหนบ้าง ไม่ใส่หน้ากากออกจากบ้าน ป...
555     เงินเข้าวันนี้ เยียวยา กลุ่มเปราะบาง รับครั้งเ...
846     "คนละครึ่ง" เตรียมพร้อมให้รับสิทธิ์เงิน 3,000 ...
280     ครม.ไฟเขียวจ่าย "เยียวยากลุ่มเปราะบาง" 13ล้านค...
72      ใครบ้าง เข้าเกณฑ์ได้รับเงิน "เราไม่ทิ้งกัน" จา...
1541                    คลัง กู้เพิ่ม7แสนล้านบาท สู้โควิด
901     เริ่มแล้ววันนี้! ลงทะเบียน คนละครึ่ง รับสิทธิเ...
1566    ข่าวปลอม อย่าแชร์! ธปท. ปล่อยคลิปเสียง แจกแจงแ...
Name: headline, dtype: object

## วัดความแม่นยำการค้นคืนด้วยจำนวนข่าวที่ต่างกัน (ข่าวที่มี similarity สูงสุด 1, 3, 5, 10 ข่าว)

In [271]:
top_1 = 0
top_3 = 0
top_5 = 0
top_10 = 0
top_30 = 0

missing_query_count = 0

not_matched = []
top10_matched_headline_only = []

for user_input in range(len(dup_del_matched_list)):
    tmp = []
    top10_tmp = []
    if dup_del_matched_list[user_input][0] == '':
        missing_query_count += 1
        continue
    
    all_result = cosine_similarity_T(20, dup_del_matched_list[user_input][0])
    
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline']):
        top_1 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline']):
        top_3 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[3]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[4]['headline']):
        top_5 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[3]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[4]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[5]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[6]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[7]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[8]['headline']) or (dup_del_matched_list[user_input][1] == all_result.iloc[9]['headline']):
        top_10 += 1
        for i in range(10):
            if dup_del_matched_list[user_input][1] == all_result.iloc[i]['headline']:
                top10_tmp.append(dup_del_matched_list[user_input][0])
                top10_tmp.append(all_result.iloc[i]['headline'])
                for i in range(20):
                    top10_tmp.append(all_result.iloc[i]['headline'])
                
                top10_matched_headline_only.append(top10_tmp)

    else:
        tmp.append(dup_del_matched_list[user_input][0])
        tmp.append(dup_del_matched_list[user_input][1])
        
        for i in range(20):
            tmp.append(all_result.iloc[i]['headline'])
            
        not_matched.append(tmp)

In [272]:
missing_query_count

0

In [273]:
top_1

1028

In [274]:
top_3

1248

In [275]:
top_5

1323

In [276]:
top_10

1391

In [277]:
len(dup_del_matched_list)

1611

In [278]:
top_10/(len(dup_del_matched_list) - missing_query_count)

0.8634388578522657

In [280]:
len(not_matched)

220

In [281]:
top_10 + len(not_matched)

1611

In [282]:
len(dup_del_matched_list) - missing_query_count

1611

# Headline and content

In [283]:
def read_cofact_refer(): #สำหรับดึงข้อมูลของ cofact csv
    
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Cofact/old/cofact_refer_old.csv')
    
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)

    # read header from CSV file
    header = []
    header = next(csvreader)
    
    rows = []
    dup_check = []
    
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        # เพิ่ม header + content และตรวจสอบว่า header ซ้ำหรือไม่
        if row[1] in dup_check:
            continue
        
        elif row[1] not in dup_check:
            dup_check.append(row[1])
            content_parts = literal_eval(row[2])
            content = ''.join(filter(None, content_parts))
            tmp.append(row[1] + content) 

        # เพิ่ม content
        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        
        tmp.append(content)
        
        # เพิ่ม link (ข่าวต้นทางสุด)
        tmp.append(row[3])
        
        # เพิ่ม link (ลิงค์บนเว็บไซต์ cofact)
        tmp.append(row[5])
        
        # เพิ่ม header
        tmp.append(row[1])
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [284]:
cofact_refer_text_list = read_cofact_refer()

In [285]:
len(cofact_refer_text_list)

2050

In [286]:
matched_list = []

for i in range(len(cofact_refer_text_list)):
    for j in range(len(cofact_info_text_list)):
        tmp = []
        if cofact_info_text_list[j][1] == cofact_refer_text_list[i][3]:
            tmp.append(cofact_info_text_list[j][0])
            tmp.append(cofact_refer_text_list[i][0])
            matched_list.append(tmp)

In [287]:
len(matched_list)

1704

### นำ query ซ้ำใน matched list ออก

In [288]:
matched_list_dup_check = []
dup_del_matched_list = []

for query in matched_list:
    if query[0] in matched_list_dup_check:
        continue
    elif query[0] not in matched_list:
        matched_list_dup_check.append(query[0])
        dup_del_matched_list.append(query)

In [289]:
len(dup_del_matched_list)

1611

In [290]:
all_refer_text_list = []
all_refer_text_list = cofact_refer_text_list

In [291]:
len(all_refer_text_list)

2050

## ------------------------------------------------------------------------------
## สร้าง dataframe ของ cofact สำหรับอ้างถึงตอนแนบลิงค์ url แสดงผล

In [292]:
all_refer_header_and_content = []
all_refer_content = []
all_refer_url = []
all_refer_datetime = []
all_refer_domain = []
all_refer_header = []

for i in range(len(all_refer_text_list)):
    all_refer_header_and_content.append(all_refer_text_list[i][0]) #list ของส่วนหัวข้อข่าว + เนื้อหา
    all_refer_content.append(all_refer_text_list[i][1]) #list ของส่วนเนื้อหาเท่านั้น
    all_refer_url.append(all_refer_text_list[i][2]) #list ของ url เท่านั้น
    all_refer_datetime.append(all_refer_text_list[i][3]) #list ของ datetime เท่านั้น
    all_refer_domain.append(urlparse(all_refer_text_list[i][2]).hostname) #list ของ domain เท่านั้น
    all_refer_header.append(all_refer_text_list[i][4]) #list ของส่วนหัวข้อข่าวเท่านั้น


In [293]:
#ทำ list ให้เป็น dataframe
all_original_text_and_headline_news_df = pd.DataFrame(list(zip(all_refer_header_and_content, all_refer_content, all_refer_url, all_refer_datetime, all_refer_domain, all_refer_header)), columns=["All_headline_and_content_from_every_reference", "All_content_from_every_reference", "All_URL_from_every_reference", "All_datatime_from_every_reference", "All_domain_from_every_reference", "All_headline_from_every_reference"])

all_original_text_and_headline_news_df

All_headline_and_content_from_every_reference  \
0     น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเ...   
1     มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อเอาอีกแ...   
2     อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสแล...   
3     ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง ก...   
4     คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริงแชร์...   
...                                                 ...   
2045  โควิด-19 : นมตราหมี ยาฆ่าพยาธิ และน้ำมันหอมระเ...   
2046  โควิด : WHO ให้ชื่อ "โอไมครอน" สายพันธุ์ใหม่ที...   
2047  ยูเอ็นเปิดผลศึกษาคดีข่มขืนในไทย-เวียดนาม ผู้หญ...   
2048  WHO : อุบัติเหตุบนท้องถนนทำให้คนหนุ่มสาวเสียชี...   
2049  ศูนย์จีโนมฯ ระบุโควิด- 19 ใกล้ End game กลายเป...   

                       All_content_from_every_reference  \
0     มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรัก...   
1     เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว...   
2     อย. เตือน!! อย่าหลงเชื่อผลิตภัณฑ์ NANO SILVER ...   
3     กาแฟเป็นเครื่องดื่มที่นิยมอย่างแพร่หลายทั่วโลก...   
4     แชร์ทั่วอินเทอร์เน็ตว่า มีคนนำปิโตรเลียม เจลลี...   
...                                                 ...   
2045  โรงพยาบาลต่าง ๆ กำลังประสบปัญหาคนไข้ล้น และการ...   
2046  WHO แถลงเมื่อวันที่ 26 พ.ย. ว่าเชื้อนี้มีการกล...   
2047  องค์การเพื่อการส่งเสริมความเสมอภาคระหว่างเพศแล...   
2048  WHO เผยแพร่ตัวเลขที่ชี้ให้เห็นว่าทวีปแอฟริกามี...   
2049  ศูนย์จีโนมทางการแพทย์ คณะแพทย์ศาสตร์ โรงพยาบาล...   

                           All_URL_from_every_reference  \
0     https://sure.oryor.com/index.php/detail/media_...   
1     https://sure.oryor.com/index.php/detail/media_...   
2     https://oryor.com/%E0%B8%AD%E0%B8%A2/detail/me...   
3     https://sure.oryor.com/index.php/detail/media_...   
4     https://sure.oryor.com/index.php/detail/media_...   
...                                                 ...   
2045    https://www.bbc.com/thai/international-57901266   
2046    https://www.bbc.com/thai/international-59428316   
2047         https://www.bbc.com/thai/thailand-42170733   
2048    https://www.bbc.com/thai/international-46545106   
2049          https://news.thaipbs.or.th/content/311692   

             All_datatime_from_every_reference  \
0     https://cofact.org/article/18fondmkdx5t1   
1      https://cofact.org/article/rzoplz5v22rb   
2     https://cofact.org/article/110yfgvyqqj5d   
3     https://cofact.org/article/2wmt8eex5xqcg   
4     https://cofact.org/article/288f0qlim28fh   
...                                        ...   
2045  https://cofact.org/article/1zctvpcnaf09t   
2046   https://cofact.org/article/lbsaldkysx4t   
2047  https://cofact.org/article/1r33jgmldh36l   
2048   https://cofact.org/article/7pxib0bvohpq   
2049  https://cofact.org/article/1wia7tfbojy4q   

     All_domain_from_every_reference  \
0                     sure.oryor.com   
1                     sure.oryor.com   
2                          oryor.com   
3                     sure.oryor.com   
4                     sure.oryor.com   
...                              ...   
2045                     www.bbc.com   
2046                     www.bbc.com   
2047                     www.bbc.com   
2048                     www.bbc.com   
2049              news.thaipbs.or.th   

                      All_headline_from_every_reference  
0     น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเ...  
1               มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ  
2     อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสแล...  
3         ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง   
4            คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริง  
...                                                 ...  
2045  โควิด-19 : นมตราหมี ยาฆ่าพยาธิ และน้ำมันหอมระเ...  
2046  โควิด : WHO ให้ชื่อ "โอไมครอน" สายพันธุ์ใหม่ที...  
2047  ยูเอ็นเปิดผลศึกษาคดีข่มขืนในไทย-เวียดนาม ผู้หญ...  
2048  WHO : อุบัติเหตุบนท้องถนนทำให้คนหนุ่มสาวเสียชี...  
2049  ศูนย์จีโนมฯ ระบุโควิด- 19 ใกล้ End game กลายเป...  

[2050 rows x 6 columns]

In [294]:
all_headline_and_content_tokens_list = [split_word(txt) for txt in all_refer_header_and_content] #นำ list ของหัวข้อข่าวมาตัดคำ

In [295]:
all_tokens_list_j = [','.join(tkn) for tkn in all_headline_and_content_tokens_list]

----------------------------------------------------------------------------------
# สร้าง vocabulary set

In [296]:
print(all_tokens_list_j[0].split(",")[0:2])


['น้ำชา', 'รักษาโรค']


In [297]:
## Create Vocabulary
tokens_list = []

for words in all_tokens_list_j:
    # print(words)
    temp_list = words.split(",")
    # print(temp_list)
    for i in temp_list:
        tokens_list.append(i)

vocabulary = set(tokens_list)
vocabulary = list(vocabulary)

In [298]:
len(vocabulary)

19290

--------------------------------------------------------------------------------------

In [299]:
tvec = TfidfVectorizer(analyzer=lambda x:x.split(','),)
original_c_feat = tvec.fit_transform(all_tokens_list_j)

### Save Trained TFID Model

In [300]:
### Save model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
with open(path,'wb') as handle:
    pickle.dump(original_c_feat, handle)

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


In [301]:
### load model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
t = pickle.load(open(path,'rb'))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


### Save Vocabulary

In [302]:
### Save Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "w", encoding="utf-8") as file:
    file.write(str(vocabulary))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [303]:
### load Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "r", encoding="utf-8") as file:
    data2 = eval(file.readline())

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [304]:
data2

['',
 'มีพิษ',
 'พริก',
 'ความสบายใจ',
 'แบน',
 'เมอร์ส',
 'ผู้ยิ่งใหญ่',
 '1.57',
 'ตระหนก',
 'Brush',
 'น้ำมัน',
 'known',
 'แสวงบุญ',
 'สัจ',
 '366',
 '102',
 'เบญจา',
 'หงสา',
 '912.',
 'ตี้',
 'หมอง',
 'หัวเข่า',
 'นาวาอากาศเอก',
 'San',
 'แอ็ค',
 'ตกอยู่ในอันตราย',
 'หัวนอน',
 'ภัยธรรมชาติ',
 '290',
 'ใบเสร็จ',
 'บ้า',
 'เทคนิค',
 'ไฮบริด',
 'เป็นไปได้',
 'หายใจ',
 'เครื่องคอมพิวเตอร์',
 'Heparin-PF',
 'วัสดุ',
 'ค้นคว้า',
 '37.2',
 'UNESCO',
 'น้ำแข็ง',
 'ได้คิด',
 'ดำริ',
 'เมตาบอลิก',
 'ข่าว',
 'ชกา',
 'พันธ์',
 'แบ่งรับแบ่งสู้',
 'RD',
 'หลอดลม',
 'เคาน์เตอร์',
 'ปลื้ม',
 'ตุ่ม',
 'แต่งหน้า',
 'ปฐมวัย',
 'เชลยศึก',
 'สมอพิเภก',
 'ธี',
 'ควน',
 'ภาษาอังกฤษ',
 'คนงาน',
 'ที่เกิด',
 'น้ำคร่ำ',
 'อำเภอ',
 'ลำพัง',
 'wave',
 'ส้น',
 'เสื่อมเสีย',
 '1678',
 'แบกรับ',
 'ฟิช',
 '427',
 'เลื่อนนัด',
 'mwectgoth',
 'ขับรถ',
 'european',
 'ลิ้ม',
 'ที่ว่าง',
 '))',
 'คิ้ว',
 'ผู้ประกอบการรายย่อย',
 'บันทึกเสียง',
 '09.42',
 'อารมณ์ไม่ดี',
 'การตรวจจับ',
 'chemotherapy',
 'ลงข่าว',
 'พล.

In [305]:
len(data2)

19290

## Create vector for Query/search keywords

In [306]:
## Create vector for Query/search keywords
def gen_vector_T(tokens):

    Q = np.zeros((len(vocabulary)))
    
    x = tvec.transform(tokens)
    
    x = x.A[0]
    return x

### Calculate Cosine similarity of trained Tfidf to input query


In [307]:
norm_original_c_feat = normalize(original_c_feat)
norm_original_c_feat = norm_original_c_feat.toarray()
norm_original_c_feat = norm_original_c_feat.T

In [308]:
query_vector = []
def cosine_similarity_T(k, query):
    tokens = split_word(str(query))
    q_df = pd.DataFrame(columns=['q_clean'])
    q_df.loc[0,'q_clean'] =str(tokens)

    q_df=q_df.replace(to_replace ="\[.", value = '', regex = True)
    q_df=q_df.replace(to_replace ="'", value = '', regex = True)
    q_df=q_df.replace(to_replace =" ", value = '', regex = True)
    q_df=q_df.replace(to_replace ='\]', value = '', regex = True)
    
    d_cosines = []
    
    query_vector = gen_vector_T(q_df['q_clean'])
    query_vector = query_vector.reshape((1,-1))

    d_cosines = np.dot(normalize(query_vector),norm_original_c_feat)
    
    list_d_cosines = d_cosines[0].tolist()
    
    out = np.array(list_d_cosines).argsort()[-k:][::-1]

    list_d_cosines.sort()
    a = pd.DataFrame()
    for i in out:
        a.loc[i,'index'] = str(i)
        a.loc[i,'headline_and_content'] = all_original_text_and_headline_news_df["All_headline_and_content_from_every_reference"][i]

    list_d_cosines.sort(reverse=True)
    
    for j in range(k):
        a.loc[out[j],'Score'] = list_d_cosines[j]
        
    return a

In [309]:
query = "สิ้นเดือนนี้ คิงส์พาวเวอร์ ปิดทุกสาขา ไม่มีกำหนด ยกเว้นสนามบิน สำนักงานใหญ่ซอยรางน้ำ ในยามปกติ ขายได้วันละ 50 ล้านบาท ตอนนี้ทุกวันขายได้วันละ 20,000 บาท"

In [310]:
%time all_result = cosine_similarity_T(30, query)

Wall time: 64 ms


In [311]:
all_result

index                               headline_and_content     Score
1310  1310    ข่าวปลอม คิงเพาเวอร์ ปิดทุกสาขาสิ้นเดือนนี้ \n   0.334849
1311  1311  “คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่า...  0.289448
1693  1693  ครม.มีมติจ่ายเงินเยียวยา "ฟรีแลนซ์" ม.39-40 คน...  0.168565
72      72  ใครบ้าง เข้าเกณฑ์ได้รับเงิน "เราไม่ทิ้งกัน" จา...  0.158405
1019  1019  เริ่มแล้ว สมอ.ควบคุมผลิต-จำหน่าย “พาวเวอร์แบงก...  0.151636
452    452  เปิดได้แล้ว! ซอยบางลา หาดป่าตอง ผับ บาร์รอ ศบค...  0.142332
1629  1629  ข่าวปลอม! นายกฯ อนุมัติ ได้คนละ 10,000 บาท ทุก...  0.135528
1444  1444  เช็ก! จังหวัดไหนบ้าง ไม่ใส่หน้ากากออกจากบ้าน ป...  0.132041
280    280  ครม.ไฟเขียวจ่าย "เยียวยากลุ่มเปราะบาง" 13ล้านค...  0.131286
1196  1196   ย้ำอีกรอบ บัตรสวัสดิการแห่งรัฐ เงินเยียวยา "เ...  0.129658
1642  1642  คกก.โรคติดต่อฯ เห็นชอบระยะห่างฉีด "แอสตราเซเนก...  0.124783
1280  1280   www.ม33เรารักกัน.com ประกันสังคมปรับเว็บไซต์ล...  0.122179
1061  1061  สธ.ประกาศห้ามขายเครื่องดื่มแอลกอฮอล์ออนไลน์ ดี...  0.119042
98      98  เตือน!อย่าหลงเชื่อข่าว เพิ่มเงินผู้รับบำนาญตาม...  0.116533
1818  1818  ข่าวปลอมรัฐแจก 25,000 บาท ชาวน่านแห่ลงทะเบียนโ...  0.116131
1963  1963  ครม. อนุมัติงบ 2.7 หมื่นล้าน ประกันรายได้และรั...  0.115409
1122  1122  ททท. สั่งชะลอเพิ่มสิทธิห้องพัก เราเที่ยวด้วยกั...  0.111790
1541  1541  คลัง กู้เพิ่ม7แสนล้านบาท สู้โควิดกระทรวงการคลั...  0.110428
555    555  เงินเข้าวันนี้ เยียวยา กลุ่มเปราะบาง รับครั้งเ...  0.109414
846    846  "คนละครึ่ง" เตรียมพร้อมให้รับสิทธิ์เงิน 3,000 ...  0.108733
843    843  ไฟเขียว "คนละครึ่ง-เพิ่มวงเงินบัตรคนจน" 29 ก.ย...  0.106710
202    202  เตือนระวังมิจฉาชีพ หลอกขาย'ตั๋วออนไลน์'ช่วงโควิด!  0.104718
177    177  อย. เตือนระวังถูกหลอก ขายแผ่นป้าย-อุปกรณ์ป้องก...  0.104034
86      86  เพิ่มเงินบำนาญ-ขยายเพดานเงินบำเหน็จ ไม่เป็นควา...  0.098328
901    901  เริ่มแล้ววันนี้! ลงทะเบียน คนละครึ่ง รับสิทธิเ...  0.097764
214    214  อย. เตือนอย่าหลงเชื่อโฆษณารับซื้อยา ส่งผลเสียท...  0.096666
1873  1873  ด่วน ครม.เคาะจ่ายเยียวยาประกันสังคม ม.33 สีแดง...  0.095858
241    241  เช็กด่วน "เยียวยานักกีฬา" กลุ่มไหนได้สิทธิ์รับ...  0.094473
389    389  ผงะ “เที่ยวปันสุข” แห่จองโดเมนเปิดเว็บ รับแจกเ...  0.093728
603    603  ธ.ออมสิน ปล่อยเงินกู้ฉุกเฉิน 5 หมื่นบาท ดอกเบี...  0.092498

In [312]:
all_result.iloc[1]['headline_and_content']

'“คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่าวเท็จ! รางน้ำ-พัทยา-ภูเก็ตเปิดตามปกติวันนี้ (16 มี.ค.) จากกรณีที่ในโซเชียลมีเดียมีการเผยแพร่และส่งต่อข้อความ ระบุว่าสิ้นเดือนนี้ คิงเพาเวอร์ ปิดทุกสาขาไม่มีกำหนด ยกเว้นสนามบิน และอ้างว่าเรียกเจ้าของรถบัส รถตู้ทุกแห่งมาคุยขอยกเลิกสัญญาไม่มีกำหนด ล่าสุด ทวิตเตอร์ KingPowerOfficial (@KingPowerhq) ระบุว่า “ข้อความส่งต่อดังกล่าวเป็นข่าวเท็จ”ทั้งนี้ เมื่อวันที่ 14 มี.ค. คิง เพาเวอร์ ปรับเปลี่ยนช่วงเวลาการให้บริการ โดย คิง เพาเวอร์ รางน้ำ และไทย เทสต์ ฮับ เปิดเวลา 10.00-20.00 น. ห้องอาหารลามูนปิดให้บริการ, คิง เพาเวอร์ พัทยา เปิดเวลา 12.00-19.00 น. ภัตตาคารรามายานะปิดให้บริการ, คิง เพาเวอร์ ภูเก็ต เปิดเวลา 11.00-19.00 น. ภัตตาคารรามายานะ เปิดให้บริการ 2 รอบ ได้แก่ 11.00-14.00 น. และ 16.00-18.00 น.ส่วนผู้ที่มีความประสงค์จะใช้บริการที่ คิง เพาเวอร์ ศรีวารี สามารถเลือกใช้บริการที่ คิง เพาเวอร์ รางน้ำ แทนได้ ในช่วงระยะเวลาดังกล่าว'

In [313]:
all_result.iloc[:10]['headline_and_content']

1310      ข่าวปลอม คิงเพาเวอร์ ปิดทุกสาขาสิ้นเดือนนี้ \n 
1311    “คิง เพาเวอร์” แจงข้อความว่อน “ปิดทุกสาขา” ข่า...
1693    ครม.มีมติจ่ายเงินเยียวยา "ฟรีแลนซ์" ม.39-40 คน...
72      ใครบ้าง เข้าเกณฑ์ได้รับเงิน "เราไม่ทิ้งกัน" จา...
1019    เริ่มแล้ว สมอ.ควบคุมผลิต-จำหน่าย “พาวเวอร์แบงก...
452     เปิดได้แล้ว! ซอยบางลา หาดป่าตอง ผับ บาร์รอ ศบค...
1629    ข่าวปลอม! นายกฯ อนุมัติ ได้คนละ 10,000 บาท ทุก...
1444    เช็ก! จังหวัดไหนบ้าง ไม่ใส่หน้ากากออกจากบ้าน ป...
280     ครม.ไฟเขียวจ่าย "เยียวยากลุ่มเปราะบาง" 13ล้านค...
1196     ย้ำอีกรอบ บัตรสวัสดิการแห่งรัฐ เงินเยียวยา "เ...
Name: headline_and_content, dtype: object

## วัดความแม่นยำการค้นคืนด้วยจำนวนข่าวที่ต่างกัน (ข่าวที่มี similarity สูงสุด 1, 3, 5, 10 ข่าว)

In [314]:
top_1 = 0
top_3 = 0
top_5 = 0
top_10 = 0
top_30 = 0

missing_query_count = 0

not_matched = []
top10_matched_headline_and_content = []

for user_input in range(len(dup_del_matched_list)):
    tmp = []
    top10_tmp = []
    if dup_del_matched_list[user_input][0] == '':
        missing_query_count += 1
        continue
    
    all_result = cosine_similarity_T(20, dup_del_matched_list[user_input][0])
    
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline_and_content']):
        top_1 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline_and_content']):
        top_3 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[3]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[4]['headline_and_content']):
        top_5 += 1
    if (dup_del_matched_list[user_input][1] == all_result.iloc[0]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[1]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[2]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[3]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[4]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[5]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[6]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[7]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[8]['headline_and_content']) or (dup_del_matched_list[user_input][1] == all_result.iloc[9]['headline_and_content']):
        top_10 += 1
        for i in range(10):
            if dup_del_matched_list[user_input][1] == all_result.iloc[i]['headline_and_content']:
                top10_tmp.append(dup_del_matched_list[user_input][0])
                top10_tmp.append(all_result.iloc[i]['headline_and_content'])
                for i in range(20):
                    top10_tmp.append(all_result.iloc[i]['headline_and_content'])
                
                top10_matched_headline_and_content.append(top10_tmp)
                
    else:
        tmp.append(dup_del_matched_list[user_input][0])
        tmp.append(dup_del_matched_list[user_input][1])
        
        for i in range(20):
            tmp.append(all_result.iloc[i]['headline_and_content'])
            
        not_matched.append(tmp)

In [315]:
missing_query_count

0

In [316]:
top_1

1123

In [317]:
top_3

1345

In [318]:
top_5

1403

In [319]:
top_10

1455

In [320]:
len(dup_del_matched_list)

1611

In [321]:
top_10/(len(dup_del_matched_list) - missing_query_count)

0.9031657355679702

In [322]:
len(not_matched)

156

In [323]:
top_10 + len(not_matched)

1611

In [324]:
len(dup_del_matched_list) - missing_query_count

1611

# Headline only vs. Headline and Content

## ข่าวที่เพิ่มมาใน result หลังจากทำ Headline + content

In [327]:
headline_only_query = []
headline_and_content_query = []

for i in range(len(top10_matched_headline_only)):
    headline_only_query.append(top10_matched_headline_only[i][0])
    
for j in range(len(top10_matched_headline_and_content)):
    headline_and_content_query.append(top10_matched_headline_and_content[j][0])

In [328]:
added_after_headline_and_content = []
for i in range(len(headline_and_content_query)):
    tmp = []
    if headline_and_content_query[i] not in headline_only_query:
        for j in range(22):
            tmp.append(top10_matched_headline_and_content[i][j])
        added_after_headline_and_content.append(tmp)

In [329]:
added_after_headline_and_content

[['เชื้อไวรัสโคโรนาจะไม่ทนต่อการเปลี่ยนแปลงของอุณหภูมิของสิ่งแวดล้อม อีกทั้งยังมีระยะเวลาการขนส่งนาน จำนวนไวรัสที่เหลือรอดมีน้อยดีที่สุด และควรเช็ดแอลกอฮอล์สิ่งของที่ส่งมาก่อนใช้',
  'นักช็อปต้องรู้ สั่งของจากจีน เสี่ยงติด "ไวรัสโคโรน่า" ขนาดไหนคุณหมอจากเพจดัง ไขข้อข้องใจนักช็อปออนไลน์  เสี่ยงติด "ไวรัสโคโรน่า" ขนาดไหน\xa0\xa0จากกรณีการระบาดของ\xa0\xa0หรือ โรคทางเดินหายใจร้ายแรง ที่เกิดจาก ข้ามสปีชีส์จากค้างคาวผ่านงูเห่ามาติดเชื้อในคน ก่อให้เกิดโรคปอดอักเสบ เริ่มระบาดในประเทศจีน เมืองอู่ฮั่น มณฑลเหอเป่ย ตั้งแต่วันที่ 31 ธันวาคม 2562 ซึ่งล่าสุด ตัวเลขผู้ติดเชื้อทั่วโลก รวม 2,800 คน เสียชีวิตแล้ว 80 ราย และหายแล้ว 57 ราย ส่วนสถานการณ์ในไทยพบผู้ติดเชื้อแล้ว 8 ราย สามารถกลับบ้านได้แล้ว 5 ราย ตามที่เสนอข่าวไปแล้วนั้นซึ่งอีกหนึ่งความกังวล อาจเป็นของนักช็อปตัวยง ที่สงสัยว่า การสั่งซื้อสินค้าออนไลน์จากประเทศจีนนั้น สามารถติดเชื้อไวรัสอู่ฮั่น หรือ ไวรัสโคโรน่า ได้หรือไม่โดยเฟซบุ๊กเพจ “” ได้แนะนำว่า การป้องกันเชื้อ ก็เหมือนป้องกันไข้หวัดใหญ่บวกอาหารเป็นพิษ คือ กินร้อน ช้อนกลาง ล้างมือ ถือตัว ไม่

In [330]:
len(added_after_headline_and_content)

100

## ข่าวที่หลุดจาก result หลังจากทำ Headline + content

In [337]:
losed_after_headline_and_content = []
for i in range(len(not_matched)):
    tmp = []
    if not_matched[i][0] in headline_only_query:
        for j in range(22):
            tmp.append(not_matched[i][j])
        losed_after_headline_and_content.append(tmp)

In [338]:
losed_after_headline_and_content

[['กระทรวงสาธารณสุข ยันไม่สามารถติดต่อได้จากการที่มองตากัน แต่การจะติดเชื้อนั้นเกิดจากเมื่อผู้ติดเชื้อมีการไอหรือจาม แล้วมีละอองออกมาข้างนอก',
  'เชื้อไวรัสโคโรนาสายพันธุ์ใหม่ สามารถติดต่อผ่านการมองตาได้ ข่าวปลอม สร้างความเข้าใจผิด อย่าแชร์!ตามที่มีข่าวปรากฏในสื่อต่างๆ ในประเด็นเรื่อง จากที่มีข่าวว่าเชื้อไวรัสโคโรนาสายพันธซึ่งอาการขอที่ที่มีความเสี่ยงติดเชื้อไวรัสโคโรนา สายพันธุ์ใหม่ คือมีไข้ ร่วมกับมีอาการระบบทางเดินหายใจ เช่น ไอ เจ็บคอ มีน้ำมูก และเหนื่อยหอบ อย่างใดอย่างหนึ่ง และหากมีประวัติการเดินทางไปเมืองอู่ฮั่น ขอให้เข้ารับการรักษาโดยด่วน ส่วนวิธีการป้องกันเองสธ.ได้แนะนำให้ประชาชนรับประทานอาหารที่ปรุงสุก ใช้ช้อนกลาง หมั่นล้างมือด้วยน้ำสบู่ หรือแอลกอฮอล์เจล และหลีกเลี่ยง การสัมผัส ใกล้ชิด กับผู้ที่มีอาการคล้ายเป็นไขหวัด มีการไอ มีน้ำมูกดังนั้นขอให้ประชาชนอย่าหลงเชื่อ และขอความร่วมมือไม่ส่ง หรือแชร์ข้อมูลดังกล่าวต่อในช่องทางสื่อสังคมออนไลน์ต่างๆ และเพื่อให้ประชนได้รับข้อมูลข่าวสาร เกี่ยวกับเชี้อไวรัสโคโรนา สถานการณ์ปัจจุบัน และการป้องกันตนเองจากเชื้อไวรัส โดยกรมควบคุมโรค กระทรวงสาธ

In [339]:
len(losed_after_headline_and_content)

36